Removing hair my converting into grayscaleand appliyin median filter

In [7]:
import os
import cv2

def preprocess_images(input_dir, output_dir, resize_dim=224, filter_size=5):
    """
    Preprocess images by resizing, converting to grayscale, and applying a median filter.
    """
    # Create output directory if it doesn't exist
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)

    # Iterate over images in input directory
    for filename in os.listdir(input_dir):
        if filename.endswith('.jpg'):
            # Load image and resize
            img_path = os.path.join(input_dir, filename)
            img = cv2.imread(img_path)
            img_resized = cv2.resize(img, (resize_dim, resize_dim))

            # Convert to grayscale
            gray = cv2.cvtColor(img_resized, cv2.COLOR_BGR2GRAY)

            # Apply median filter
            filtered = cv2.medianBlur(gray, filter_size)

            # Save preprocessed image
            out_path = os.path.join(output_dir, filename)
            cv2.imwrite(out_path, filtered)
input_dir = 'HAM10000_images'
output_dir = 'preprocessed_images'
preprocess_images(input_dir, output_dir)


Creating preprocessed.csv file


In [1]:
import pandas as pd
import os

# Define path for preprocessed images
preprocessed_path = 'preprocessed_images'

# Read HAM10000 metadata
metadata = pd.read_csv('HAM10000_metadata.csv')

# Define columns for preprocessed_data.csv
columns = ['image_id', 'dx', 'age', 'sex', 'localization', 'path']

# Create empty dataframe to store preprocessed data
preprocessed_data = pd.DataFrame(columns=columns)

# Loop through each row in metadata and add preprocessed image path to preprocessed_data
for index, row in metadata.iterrows():
    image_id = row['image_id']
    dx = row['dx']
    age = row['age']
    sex = row['sex']
    localization = row['localization']
    path = os.path.join(preprocessed_path, image_id + '.jpg')
    preprocessed_data = preprocessed_data.append({'image_id': image_id, 'dx': dx, 'age': age, 'sex': sex, 'localization': localization, 'path': path}, ignore_index=True)

# Save preprocessed_data to csv
preprocessed_data.to_csv('preprocessed_data.csv', index=False)


C:\Users\hp\AppData\Local\Temp\ipykernel_28624\60605511.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  preprocessed_data = preprocessed_data.append({'image_id': image_id, 'dx': dx, 'age': age, 'sex': sex, 'localization': localization, 'path': path}, ignore_index=True)
C:\Users\hp\AppData\Local\Temp\ipykernel_28624\60605511.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  preprocessed_data = preprocessed_data.append({'image_id': image_id, 'dx': dx, 'age': age, 'sex': sex, 'localization': localization, 'path': path}, ignore_index=True)
C:\Users\hp\AppData\Local\Temp\ipykernel_28624\60605511.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  preprocessed_data = preprocessed_data.append({'image_id': image_id, 'dx': 

Data Augumentation

In [12]:
import os
import numpy as np
import pandas as pd
from PIL import Image
from tensorflow.keras.preprocessing.image import ImageDataGenerator
import cv2

# Load preprocessed data
preprocessed_data = pd.read_csv('preprocessed_data.csv')

# Select classes for augmentation
selected_classes = ['bcc', 'akiec', 'vasc', 'df']

# Create data generators for augmentation
datagen = ImageDataGenerator(
    rotation_range=20,
    width_shift_range=0.1,
    height_shift_range=0.1,
    zoom_range=0.1,
    horizontal_flip=True,
    vertical_flip=True,
    fill_mode='reflect'
)

# Loop through selected classes
for cls in selected_classes:
    # Get image IDs for class
    image_ids = preprocessed_data.loc[preprocessed_data['dx'] == cls, 'image_id']
    
    # Check if class has less than 100 images
    if len(image_ids) < 550:
        # Create folder for augmented images
        os.makedirs(f'preprocessed_images/{cls}_augmented', exist_ok=True)
        
        # Loop through image IDs
        for img_id in image_ids:
            # Load image
            img = Image.open(f'preprocessed_images/{img_id}.jpg')
            img_gray = cv2.imread(f'preprocessed_images/{img_id}.jpg', cv2.IMREAD_GRAYSCALE)
            # Convert to RGB
            img_rgb = cv2.cvtColor(img_gray, cv2.COLOR_GRAY2RGB)

            img = img_rgb

            # Convert to numpy array
            x = np.array(img)
            #x = np.expand_dims(x, axis=0)  # add an extra dimension for batch size
            #x = np.expand_dims(x, axis=-1)  # add an extra dimension for num_channels
            x = x.reshape((1,) + x.shape)
            
            # Generate 2 augmented images
            i = 0
            for batch in datagen.flow(x, batch_size=1,
                                      save_to_dir=f'preprocessed_images/{cls}_augmented',
                                      save_prefix=f'{img_id}_aug',
                                      save_format='jpg'):
                i += 1
                if i >= 2:
                    break


Splitting the data

In [13]:
from sklearn.model_selection import train_test_split

# Load preprocessed data as a pandas dataframe
preprocessed_data = pd.read_csv('preprocessed_data.csv')

# Split data into training and validation sets
train_data, val_data = train_test_split(preprocessed_data, test_size=0.2, random_state=42)

# Save training and validation sets as CSV files
train_data.to_csv('train_data.csv', index=False)
val_data.to_csv('val_data.csv', index=False)


Segmentation with GAC

In [19]:
"""import os
import numpy as np
import pandas as pd
from skimage import io
from skimage.filters import threshold_otsu
from skimage.segmentation import active_contour

# Load preprocessed data
preprocessed_data = pd.read_csv('preprocessed_data.csv')

# Select a single image to segment
image_id = preprocessed_data.iloc[4349]['image_id']
img_path = f'preprocessed_images/{image_id}.jpg'

# Load the image
img = io.imread(img_path)

# Apply Otsu thresholding
thresh = threshold_otsu(img)
binary = img > thresh

# Initialize the GAC algorithm with initial contour
s = np.linspace(0, 2*np.pi, 400)
r = 100 + 50*np.sin(s)
c = 100 + 50*np.cos(s)
init = np.array([r, c]).T
snake = active_contour(binary, init, alpha=0.1, beta=1, gamma=0.01)

# Save the segmented image
io.imsave(f'segmented_images/{image_id}.jpg', binary)
"""

C:\Users\hp\AppData\Local\Temp\ipykernel_28624\2665730713.py:30: UserWarning: segmented_images/ISIC_0024306.jpg is a boolean image: setting True to 255 and False to 0. To silence this warning, please convert the image using img_as_ubyte.
  io.imsave(f'segmented_images/{image_id}.jpg', binary)


Segmentation with otsu and GAC

In [20]:
import cv2
import numpy as np
import pandas as pd
from skimage.segmentation import active_contour

# Load preprocessed data
preprocessed_data = pd.read_csv('preprocessed_data.csv')

# Loop through preprocessed images
for idx, row in preprocessed_data.iterrows():
    # Load image
    img_path = f'preprocessed_images/{row["image_id"]}.jpg'
    img = cv2.imread(img_path)

    # Convert to grayscale
    gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)

    # Apply Otsu thresholding
    _, thresh = cv2.threshold(gray, 0, 255, cv2.THRESH_BINARY+cv2.THRESH_OTSU)

    # Initialize snake contour
    init_contour = np.array([[0, 0], [0, 1], [1, 1], [1, 0]])

    # Apply GAC
    snake = active_contour(thresh, init_contour, alpha=0.1, beta=1.0, gamma=0.01)

    # Save segmented image
    seg_path = f'segmented_images/{row["image_id"]}.jpg'
    cv2.imwrite(seg_path, thresh)


Feature Extraction Using ABCD algorithm segmented images eith original image


In [8]:
import cv2
import numpy as np
import pandas as pd
import os

segmented_image_dir = 'segmented_images'
segmented_images = [os.path.join(segmented_image_dir, f) for f in os.listdir(segmented_image_dir) if os.path.isfile(os.path.join(segmented_image_dir, f))]

# create empty lists to store ABCD values
asymmetry = []
border_irregularity = []
color_variation = []
diameter = []
# loop through segmented images
for i in range(len(segmented_images)):
    img = cv2.imread(segmented_images[i], 0)
    img = cv2.threshold(img, 0, 255, cv2.THRESH_BINARY)[1]

    # calculate image moments and centroid
    M = cv2.moments(img)
    cX = int(M["m10"] / M["m00"])
    cY = int(M["m01"] / M["m00"])

    # calculate image perimeter and area
    contours, hierarchy = cv2.findContours(img, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    perimeter = cv2.arcLength(contours[0], True)
    area = cv2.contourArea(contours[0])

    # calculate asymmetry
    asymmetry.append(cv2.matchShapes(contours[0], contours[0], 1, 0.0))

    # calculate border irregularity
    if area > 0:
        border_irregularity.append((perimeter ** 2) / (4 * np.pi * area))
    else:
        border_irregularity.append(0)


    # calculate color variation
    color_variation.append(cv2.mean(img)[0])

    # calculate diameter
    diameter.append(np.sqrt((4 * area) / np.pi))
    #print(i, end= "")

# create dataframe to store ABCD values
abcd_df = pd.DataFrame({
    'Image': segmented_images,
    'Asymmetry': asymmetry,
    'Border Irregularity': border_irregularity,
    'Color Variation': color_variation,
    'Diameter': diameter
})

# save dataframe to csv file
abcd_df.to_csv('abcd_values.csv', index=False)


Feature selection


In [11]:
"""import pandas as pd
from sklearn.feature_selection import mutual_info_regression

# Load the data
data = pd.read_csv('abcd_values.csv')

# Separate the target variable
y = data['Image']
X = data.drop(['Image'], axis=1)

# Calculate the mutual information score for each feature
mi_scores = mutual_info_regression(X, y)

# Create a DataFrame to store the scores
mi_df = pd.DataFrame({'Feature': X.columns, 'MI Score': mi_scores})

# Sort the features by their MI score in descending order
mi_df = mi_df.sort_values('MI Score', ascending=False)

# Print the DataFrame
print(mi_df)
"""

"import pandas as pd\nfrom sklearn.feature_selection import mutual_info_regression\n\n# Load the data\ndata = pd.read_csv('abcd_values.csv')\n\n# Separate the target variable\ny = data['Image']\nX = data.drop(['Image'], axis=1)\n\n# Calculate the mutual information score for each feature\nmi_scores = mutual_info_regression(X, y)\n\n# Create a DataFrame to store the scores\nmi_df = pd.DataFrame({'Feature': X.columns, 'MI Score': mi_scores})\n\n# Sort the features by their MI score in descending order\nmi_df = mi_df.sort_values('MI Score', ascending=False)\n\n# Print the DataFrame\nprint(mi_df)\n"

feature selection directly using the pre-trained CNN model

In [12]:
import tensorflow.keras as keras
import numpy as np
import cv2
import os
import pandas as pd

# Load pre-trained model
model = keras.applications.VGG16(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

# Define function to extract features from an image
def extract_features(img_path):
    img = cv2.imread(img_path)
    img = cv2.resize(img, (224, 224))
    img = keras.applications.vgg16.preprocess_input(img)
    img = np.expand_dims(img, axis=0)
    features = model.predict(img)
    features = features.flatten()
    return features

# Initialize lists for feature values
image_paths = []
features = []

# Loop through segmented images
for img_name in os.listdir("segmented_images"):
    img_path = os.path.join("segmented_images", img_name)
    image_paths.append(img_name)
    features.append(extract_features(img_path))

# Convert features list to numpy array and save to CSV file
features = np.array(features)
df = pd.DataFrame(features, columns=[f"feature_{i+1}" for i in range(features.shape[1])])
df.insert(0, "Image", image_paths)
df.to_csv("segmented_image_features.csv", index=False)


1/1 [==============================] - 0s 333ms/step


Splitting of abcd_values.csv data

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split

# Load the data from abcd_values.csv file
data = pd.read_csv('abcd_values.csv')

# Split the data into train and test sets
train_data, test_data = train_test_split(data, test_size=0.2, random_state=42)

# Save the train and test data to CSV files
train_data.to_csv('train_data.csv', index=False)
test_data.to_csv('test_data.csv', index=False)


Defining the CNN architecture

In [ ]:
import pandas as pd

# Load the preprocessed and segmented data
x = pd.read_csv('preprocessed_data.csv')
y = pd.read_csv('segmented_image_features.csv')
print(x.shape)
print(y.shape)

In [6]:
import tensorflow as tf
import pandas as pd
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout
from sklearn.model_selection import train_test_split

# define input shape
input_shape = (224, 224, 3)

# create model
model = tf.keras.Sequential([
    Conv2D(32, (3, 3), activation='relu', input_shape=input_shape),
    MaxPooling2D((2, 2)),
    Conv2D(64, (3, 3), activation='relu'),
    MaxPooling2D((2, 2)),
    Conv2D(128, (3, 3), activation='relu'),
    MaxPooling2D((2, 2)),
    Conv2D(128, (3, 3), activation='relu'),
    MaxPooling2D((2, 2)),
    Flatten(),
    Dense(512, activation='relu'),
    Dropout(0.5),
    Dense(1, activation='sigmoid')
])

# compile model
model.compile(loss='binary_crossentropy',
              optimizer=tf.keras.optimizers.Adam(lr=1e-4),
              metrics=['accuracy'])

# print model summary
#model.summary()

X = pd.read_csv('preprocessed_data.csv')
y = pd.read_csv('segmented_image_features.csv')

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

model.fit(X_train, y_train, epochs=10, batch_size=32)


y_pred = model.predict(X_test)
y_pred_binary = np.round(y_pred).flatten()
accuracy = accuracy_score(y_test, y_pred_binary)
print('Accuracy:', accuracy)


C:\Users\hp\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\keras\optimizers\optimizer_v2\adam.py:110: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)


KeyboardInterrupt: 

merge the features and metadata dataframes

In [16]:
import pandas as pd
import numpy as np
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

# Load the preprocessed and segmented data
X = pd.read_csv('preprocessed_data.csv')
y = pd.read_csv('abcd_values.csv')

# Reshape the input data to 4D tensors
X = X.values.reshape(-1, 227, 227, 1)

# Convert the target data to 1D numpy arrays
y = y['label'].values

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Define the CNN architecture
model = tf.keras.Sequential([
    tf.keras.layers.Conv2D(32, (3, 3), activation='relu', input_shape=(227, 227, 1)),
    tf.keras.layers.MaxPooling2D((2, 2)),
    tf.keras.layers.Conv2D(64, (3, 3), activation='relu'),
    tf.keras.layers.MaxPooling2D((2, 2)),
    tf.keras.layers.Dropout(0.25),
    tf.keras.layers.Conv2D(128, (3, 3), activation='relu'),
    tf.keras.layers.MaxPooling2D((2, 2)),
    tf.keras.layers.Dropout(0.25),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(512, activation='relu'),
    tf.keras.layers.Dropout(0.5),
    tf.keras.layers.Dense(1, activation='sigmoid')
])

# Compile the model with binary cross-entropy loss
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

# Train the model on the training data
model.fit(X_train, y_train, epochs=10, batch_size=32)

# Evaluate the model on the testing data
y_pred = model.predict(X_test)
y_pred_binary = np.round(y_pred).flatten()
accuracy = accuracy_score(y_test, y_pred_binary)
print('Accuracy:', accuracy)


ValueError: cannot reshape array of size 60090 into shape (227,227,1)

CNN architecture for training and testing data

In [23]:
import tensorflow as tf
import pandas as pd
import tensorflow as tf
#from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout
from sklearn.model_selection import train_test_split
import cv2

# Load the preprocessed and segmented data
#x = pd.read_csv('preprocessed_data.csv')
#y = pd.read_csv('segmented_image_features.csv')

# Define the image size to resize to
IMG_SIZE = (224, 224)

# Reshape the input data to 4D tensors
X = []
for path in x['path']:
    img = cv2.imread(path, cv2.IMREAD_GRAYSCALE)  # Load image in grayscale
    #print(img)
    img = cv2.resize(img, IMG_SIZE)  # Resize image
    img = img.reshape((*IMG_SIZE, 1))  # Reshape image to (224, 224, 1)
    X.append(img)
X = np.array(X)

# Convert the target data to 1D numpy arrays
#y = y.drop(['image_path'], axis=1)  # Drop image_path column
y = y.values

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Define the CNN architecture
model = tf.keras.Sequential([
    tf.keras.layers.Conv2D(32, (3, 3), activation='relu', input_shape=(224, 224, 1)),
    tf.keras.layers.MaxPooling2D((2, 2)),
    tf.keras.layers.Conv2D(64, (3, 3), activation='relu'),
    tf.keras.layers.MaxPooling2D((2, 2)),
    tf.keras.layers.Dropout(0.25),
    tf.keras.layers.Conv2D(128, (3, 3), activation='relu'),
    tf.keras.layers.MaxPooling2D((2, 2)),
    tf.keras.layers.Dropout(0.25),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(512, activation='relu'),
    tf.keras.layers.Dropout(0.5),
    tf.keras.layers.Dense(y.shape[1], activation='sigmoid')
])

# Compile the model with binary cross-entropy loss
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

# Train the model on the training data
model.fit(X_train, y_train, epochs=10, batch_size=32)

# Evaluate the model on the testing data
y_pred = model.predict(X_test)
y_pred_binary = np.round(y_pred).astype(int)
accuracy = accuracy_score(y_test, y_pred_binary)
print('Accuracy:', accuracy)


In [15]:
import pandas as pd

# Load the preprocessed and segmented data
x = pd.read_csv('preprocessed_data.csv')
y = pd.read_csv('segmented_image_features.csv')
print(x.shape)
print(y.shape)

(10015, 6)
(10015, 25089)
